In [1]:
import os
import random
import numpy as np
import h5py
from l3embedding.audio import pcm2float
import umap
from sklearn.manifold import TSNE
import multiprocessing
from joblib import Parallel, delayed
from functools import partial
from multiprocessing import Pool

In [2]:
def get_teacher_embedding(audio_batch):
    import keras
    import tensorflow as tf
    from kapre.time_frequency import Melspectrogram
    
    try:
        with tf.Graph().as_default(), tf.Session().as_default():
            weight_path = '/scratch/sk7898/l3pruning/embedding/fixed/reduced_input/l3_full_original_48000_256_242_2048.h5'
            model = keras.models.load_model(weight_path, custom_objects={'Melspectrogram': Melspectrogram}) 
            embeddings = model.get_layer('audio_model').predict(audio_batch)
            return embeddings

    except GeneratorExit:
        pass

In [3]:
def write_to_h5(paths, batch, batch_size):
    n_files = int(batch_size/1024)
    start_idx = 0
    
    for path in paths:
        end_idx = start_idx + 1024
            
        with h5py.File(path, 'a') as f:
            for key in batch.keys():
                if key in f.keys():
                    continue
                f.create_dataset(key, data=batch[key][start_idx:end_idx], compression='gzip')
            f.close()
        start_idx = end_idx

In [4]:
def get_reduced_embedding(data, method, emb_len=None, neighbors=10, \
                          metric='euclidean', min_dist=0.3, iterations=500):
    
    if len(data) == 0:
        raise ValueError('Data is empty!')
    if emb_len is None:
        raise ValueError('Reduced embedding dimension was not provided!')

    if method == 'umap':
        embedding = umap.umap_.UMAP(n_neighbors=neighbors, min_dist=min_dist, metric=metric, \
                                    n_components=emb_len).fit_transform(data)
    elif method == 'tsne':
        embedding = TSNE(perplexity=neighbors, n_components=emb_len, metric=metric, \
                         n_iter=iterations, method='exact').fit_transform(data)
    else:
        raise ValueError('Reduction method technique should be either `umap` or `tsne`!')
    
    return embedding

In [5]:
def get_blob_keys(method, batch_size, emb_len, neighbors_list=None, metric_list=None, min_dist_list=None, tsne_iter_list=None):
    
    blob_keys = []
    
    if method == 'umap':
        if neighbors_list is None or metric_list is None or min_dist_list is None:
            raise ValueError('Either neighbor_list or metric_list or min_dist_list is missing')
        
        [blob_keys.append('umap_batch_' + str(batch_size) + \
                          '_len_' + str(emb_len) + \
                          '_k_' + str(neighbors) + \
                          '_metric_' + metric + \
                          '_dist|iter_' + str(min_dist)) \
         for neighbors in neighbors_list for metric in metric_list for min_dist in min_dist_list]
                    
    elif method == 'tsne':
        if neighbors_list is None or metric_list is None or tsne_iter_list is None:
            raise ValueError('Either neighbor_list or metric_list or tsne_iter_list is missing')
        
        [blob_keys.append('tsne_batch_' + str(batch_size) +\
                          '_len_' + str(emb_len) + \
                          '_batch_' + str(batch_size) + \
                          '_k_' + str(neighbors) + \
                          '_metric_' + metric + \
                          '_dist|iter_' + str(iteration)) \
        for neighbors in neighbors_list for metric in metric_list for iteration in tsne_iter_list]

    return blob_keys

In [35]:
def embedding_generator(data_dir, output_dir, reduced_emb_len, approx_mode='umap', neighbors_list=None, \
                        metric_list=None, min_dist_list=None, tsne_iter_list=[500], \
                        batch_size=1024, random_state=20180123, start_batch_idx=None):

    if data_dir == output_dir:
        raise ValueError('Output path should not be same as data path to avoid overwriting data files!')
        
    if neighbors_list is None:
        raise ValueError('Neighbor cannot be None!')
    
    if metric_list is None:
        metric_list = ['euclidean']

    if approx_mode == 'umap' and min_dist_list is None:
        min_dist_list = [0.3]
    
    random.seed(random_state)
    
    batch = None
    blob_embeddings = dict()
    embedding_out_paths = []
    curr_batch_size = 0
    batch_idx = 0

    if not os.path.isdir(output_dir):
        os.makedirs(output_dir)

    blob_keys = get_blob_keys(approx_mode, batch_size, reduced_emb_len,\
                              neighbors_list=neighbors_list, metric_list=metric_list,\
                              min_dist_list=min_dist_list, tsne_iter_list=tsne_iter_list)
    
    print('Embedding Blob Keys: {}'.format(blob_keys))
        
    b_idx = 0
    for fname in os.listdir(data_dir):
        if os.path.isdir(fname):
            continue
            
        batch_path = os.path.join(data_dir, fname)
        blob_start_idx = 0

        blob = h5py.File(batch_path, 'r')
        blob_size = len(blob['label'])
        
        embedding_out_paths.append(os.path.join(output_dir, fname))

        while blob_start_idx < blob_size:
            blob_end_idx = min(blob_start_idx + batch_size - curr_batch_size, blob_size)

            # If we are starting from a particular batch, skip computing all of
            # the prior batches
            if start_batch_idx is None or batch_idx >= start_batch_idx:
                if batch is None:
                    batch = {'audio':blob['audio'][blob_start_idx:blob_end_idx]}
                else:
                    batch['audio'] = np.concatenate([batch['audio'], blob['audio'][blob_start_idx:blob_end_idx]])

            curr_batch_size += blob_end_idx - blob_start_idx
            blob_start_idx = blob_end_idx
            
            if blob_end_idx == blob_size:
                blob.close()

            if curr_batch_size == batch_size:
                results = []
                # If we are starting from a particular batch, skip yielding all
                # of the prior batches
                if start_batch_idx is None or batch_idx >= start_batch_idx:
                    # Convert audio to float
                    batch['audio'] = pcm2float(batch['audio'], dtype='float32')
                    
                    # Get the embedding layer output from the audio_model and flatten it to be treated as labels for the student audio model
                    teacher_embedding = get_teacher_embedding(batch['audio'])
                    
                    if approx_mode == 'umap':
                        n_process = len(neighbors_list) * len(metric_list) * len(min_dist_list)
                                            
                        results = Parallel(n_jobs=min(multiprocessing.cpu_count(), n_process))\
                                                    (delayed(get_reduced_embedding)(teacher_embedding, 'umap',\
                                                                                   emb_len=reduced_emb_len,\
                                                                                   neighbors=neighbors,\
                                                                                   metric=metric,\
                                                                                   min_dist=min_dist)\
                        for neighbors in neighbors_list for metric in metric_list for min_dist in min_dist_list)
                                                
                        
                    for idx in range(len(results)):
                        if blob_keys[idx] not in blob_embeddings.keys():    
                            blob_embeddings[blob_keys[idx]] = np.zeros((blob_size, reduced_emb_len), dtype=np.float32)
                            blob_embeddings[blob_keys[idx]] = results[idx]
                        else:
                            blob_embeddings[blob_keys[idx]] = results[idx]
                      
                    blob_embeddings['l3_embedding'] = teacher_embedding
                    write_to_h5(embedding_out_paths, blob_embeddings, batch_size) 
              
                    b_idx += 1
                    print('File {}: {} done!'.format(b_idx, fname))
                
                batch_idx += 1
                curr_batch_size = 0
                batch = None
                blob_embeddings = dict()
                embedding_out_paths = []

In [36]:
data_dir = '/scratch/sk7898/temp_data'
output_dir = '/scratch/sk7898/temp_emb/temp_data'
reduced_emb_len = 256
neighbors_list = [10, 20, 30]
min_dist_list = [0.3]
metric_list = ['correlation']

embedding_generator(data_dir, output_dir, reduced_emb_len, approx_mode='umap', neighbors_list=neighbors_list, \
                    metric_list=metric_list, min_dist_list=min_dist_list, \
                    batch_size=1024)

Embedding Blob Keys: ['umap_batch_1024_len_256_k_10_metric_correlation_dist|iter_0.3', 'umap_batch_1024_len_256_k_20_metric_correlation_dist|iter_0.3', 'umap_batch_1024_len_256_k_30_metric_correlation_dist|iter_0.3']


/home/sk7898/miniconda3/envs/l3embedding-new-cpu/lib/python3.6/site-packages/librosa/filters.py:261: UserWarning: Empty filters detected in mel frequency basis. Some channels will produce empty responses. Try increasing your sampling rate (and fmax) or reducing n_mels.
  warnings.warn('Empty filters detected in mel frequency basis. '
/home/sk7898/miniconda3/envs/l3embedding-new-cpu/lib/python3.6/site-packages/keras/models.py:251: UserWarning: No training configuration found in save file: the model was *not* compiled. Compile it manually.
  warnings.warn('No training configuration found in save file: '


File 1: 20180261_7_35.h5 done!
File 2: 20180261_7_34.h5 done!


In [50]:
fname = '/scratch/sk7898/reduced_embeddings/music_valid/0_0_22.h5'
blob = h5py.File(batch_path, 'r') 
print('File: ', fname)
for key in blob.keys():
    print(blob[key])
blob.close()

File:  /scratch/sk7898/reduced_embeddings/music_valid/0_0_22.h5
<HDF5 dataset "umap_batch_1024_len_256_k_10_metric_correlation_dist|iter_0.3": shape (1024, 256), type "<f4">
<HDF5 dataset "umap_batch_1024_len_256_k_20_metric_correlation_dist|iter_0.3": shape (1024, 256), type "<f4">
<HDF5 dataset "umap_batch_1024_len_256_k_30_metric_correlation_dist|iter_0.3": shape (1024, 256), type "<f4">
<HDF5 dataset "umap_batch_1024_len_256_k_5_metric_correlation_dist|iter_0.3": shape (1024, 256), type "<f4">


In [5]:
fname = '/scratch/dr2915/reduced_embeddings/umap/umap_ndata=2048000_emb=256_nbrs=10_mindist=0.3_mtrc=euclidean/music_valid/9_9_9.h5'
blob = h5py.File(fname) 
print('File: ', fname)
for key in blob.keys():
    print(blob[key])
blob.close()

File:  /scratch/dr2915/reduced_embeddings/umap/umap_ndata=2048000_emb=256_nbrs=10_mindist=0.3_mtrc=euclidean/music_valid/9_9_9.h5
<HDF5 dataset "umap_batch_2048000_len_256_k_10_metric_euclidean_dist|iter_0.3": shape (1024, 256), type "<f4">


In [34]:
#Test the multiprocessing return
reduced_emb_len = 256
neighbors_list = [10, 20, 30]
min_dist_list = [0.3, 0.5]
metric_list = ['correlation', 'euclidean']

def whatever(method, emb_len=None, neighbors=10, metric='euclidean', min_dist=0.3, iterations=500):
    dummy = neighbors
    return dummy

functions = (delayed(whatever)('umap',\
                            emb_len=reduced_emb_len,\
                            neighbors=neighbors,\
                            metric=metric,\
                            min_dist=min_dist)\
for neighbors in neighbors_list for metric in metric_list for min_dist in min_dist_list)

for f, args, kwargs in functions:
    print(f, args, kwargs)
    
results = Parallel(n_jobs=min(multiprocessing.cpu_count(),3))(delayed(whatever)('umap',\
                                                                emb_len=reduced_emb_len,\
                                                                neighbors=neighbors,\
                                                                metric=metric,\
                                                                min_dist=min_dist)\
for neighbors in neighbors_list for metric in metric_list for min_dist in min_dist_list)

print(results)

<function whatever at 0x2ae23607d598> ('umap',) {'emb_len': 256, 'neighbors': 10, 'metric': 'correlation', 'min_dist': 0.3}
<function whatever at 0x2ae23607d598> ('umap',) {'emb_len': 256, 'neighbors': 10, 'metric': 'correlation', 'min_dist': 0.5}
<function whatever at 0x2ae23607d598> ('umap',) {'emb_len': 256, 'neighbors': 10, 'metric': 'euclidean', 'min_dist': 0.3}
<function whatever at 0x2ae23607d598> ('umap',) {'emb_len': 256, 'neighbors': 10, 'metric': 'euclidean', 'min_dist': 0.5}
<function whatever at 0x2ae23607d598> ('umap',) {'emb_len': 256, 'neighbors': 20, 'metric': 'correlation', 'min_dist': 0.3}
<function whatever at 0x2ae23607d598> ('umap',) {'emb_len': 256, 'neighbors': 20, 'metric': 'correlation', 'min_dist': 0.5}
<function whatever at 0x2ae23607d598> ('umap',) {'emb_len': 256, 'neighbors': 20, 'metric': 'euclidean', 'min_dist': 0.3}
<function whatever at 0x2ae23607d598> ('umap',) {'emb_len': 256, 'neighbors': 20, 'metric': 'euclidean', 'min_dist': 0.5}
<function whatev

In [15]:
# Test the Multi-GPU callback to save single-GPU model
import keras
from kapre.time_frequency import Melspectrogram
#model_path = '/scratch/sk7898/l3pruning/embedding_approx_mse/embedding_approx/mse_original/20190912111335/model_best_valid_loss.h5'
#model_path='/scratch/sk7898/l3pruning/embedding_approx_mse/embedding_approx/mse_original/20190912113135/model_best_valid_mae.h5'
model = keras.models.load_model(model_path, custom_objects={'Melspectrogram': Melspectrogram})
embedding_shape = model.get_layer('audio_embedding_layer').output_shape
print(embedding_shape)

(None, 8, 12, 512)


/home/sk7898/miniconda3/envs/l3embedding-new-cpu/lib/python3.6/site-packages/keras/models.py:251: UserWarning: No training configuration found in save file: the model was *not* compiled. Compile it manually.
  warnings.warn('No training configuration found in save file: '


In [4]:
import os
import random
def get_dir_splits(train_data_dir, split=0.017):
    all_files = os.listdir(os.path.abspath(train_data_dir))
    #Make sure only h5 files are retrieved
    data_files = list(filter(lambda file: file.endswith('.h5'), all_files))
    
    random.shuffle(data_files)
    split_index = int(len(data_files) * split)
    train_files = data_files[:split_index]
    val_files = data_files[split_index:]
    
    return train_files, val_files

train, val = get_dir_splits('/scratch/mc6591/sonyc_ndata=60028928')

In [5]:
print(len(train))
print(len(val))

996
57624


In [10]:
if type(val) == list:
    print("List")

List


In [8]:
def cycle_shuffle(iterable, shuffle=True):
    lst = list(iterable)
    while True:
        yield from lst
        if shuffle:
            random.shuffle(lst)

In [12]:
for fname in cycle_shuffle(val):
    print(fname)

sonyc_ndata=60028928_job=16_split=1407.h5
sonyc_ndata=60028928_job=14_split=243.h5
sonyc_ndata=60028928_job=27_split=1256.h5
sonyc_ndata=60028928_job=24_split=95.h5
sonyc_ndata=60028928_job=28_split=942.h5
sonyc_ndata=60028928_job=5_split=932.h5
sonyc_ndata=60028928_job=22_split=494.h5
sonyc_ndata=60028928_job=10_split=1354.h5
sonyc_ndata=60028928_job=29_split=1618.h5
sonyc_ndata=60028928_job=12_split=1291.h5
sonyc_ndata=60028928_job=15_split=1369.h5
sonyc_ndata=60028928_job=19_split=510.h5
sonyc_ndata=60028928_job=3_split=166.h5
sonyc_ndata=60028928_job=21_split=1479.h5
sonyc_ndata=60028928_job=24_split=3.h5
sonyc_ndata=60028928_job=9_split=832.h5
sonyc_ndata=60028928_job=11_split=1654.h5
sonyc_ndata=60028928_job=14_split=1349.h5
sonyc_ndata=60028928_job=1_split=1910.h5
sonyc_ndata=60028928_job=23_split=1746.h5
sonyc_ndata=60028928_job=24_split=1279.h5
sonyc_ndata=60028928_job=8_split=198.h5
sonyc_ndata=60028928_job=21_split=1194.h5
sonyc_ndata=60028928_job=1_split=205.h5
sonyc_ndata=

sonyc_ndata=60028928_job=26_split=1269.h5
sonyc_ndata=60028928_job=20_split=635.h5
sonyc_ndata=60028928_job=19_split=1606.h5
sonyc_ndata=60028928_job=4_split=1460.h5
sonyc_ndata=60028928_job=18_split=1889.h5
sonyc_ndata=60028928_job=9_split=250.h5
sonyc_ndata=60028928_job=7_split=982.h5
sonyc_ndata=60028928_job=24_split=1045.h5
sonyc_ndata=60028928_job=19_split=1294.h5
sonyc_ndata=60028928_job=27_split=1800.h5
sonyc_ndata=60028928_job=27_split=497.h5
sonyc_ndata=60028928_job=25_split=1599.h5
sonyc_ndata=60028928_job=7_split=178.h5
sonyc_ndata=60028928_job=29_split=40.h5
sonyc_ndata=60028928_job=24_split=42.h5
sonyc_ndata=60028928_job=1_split=835.h5
sonyc_ndata=60028928_job=16_split=1802.h5
sonyc_ndata=60028928_job=18_split=965.h5
sonyc_ndata=60028928_job=19_split=591.h5
sonyc_ndata=60028928_job=22_split=1921.h5
sonyc_ndata=60028928_job=5_split=1949.h5
sonyc_ndata=60028928_job=19_split=1655.h5
sonyc_ndata=60028928_job=28_split=1664.h5
sonyc_ndata=60028928_job=20_split=637.h5
sonyc_ndata

sonyc_ndata=60028928_job=16_split=1204.h5
sonyc_ndata=60028928_job=10_split=186.h5
sonyc_ndata=60028928_job=16_split=456.h5
sonyc_ndata=60028928_job=19_split=1165.h5
sonyc_ndata=60028928_job=20_split=928.h5
sonyc_ndata=60028928_job=25_split=500.h5
sonyc_ndata=60028928_job=26_split=1892.h5
sonyc_ndata=60028928_job=22_split=897.h5
sonyc_ndata=60028928_job=22_split=613.h5
sonyc_ndata=60028928_job=24_split=1717.h5
sonyc_ndata=60028928_job=20_split=1764.h5
sonyc_ndata=60028928_job=25_split=1470.h5
sonyc_ndata=60028928_job=11_split=214.h5
sonyc_ndata=60028928_job=14_split=1924.h5
sonyc_ndata=60028928_job=19_split=849.h5
sonyc_ndata=60028928_job=7_split=71.h5
sonyc_ndata=60028928_job=19_split=1915.h5
sonyc_ndata=60028928_job=27_split=613.h5
sonyc_ndata=60028928_job=3_split=941.h5
sonyc_ndata=60028928_job=25_split=1035.h5
sonyc_ndata=60028928_job=22_split=986.h5
sonyc_ndata=60028928_job=21_split=1250.h5
sonyc_ndata=60028928_job=20_split=1768.h5
sonyc_ndata=60028928_job=23_split=219.h5
sonyc_nd

sonyc_ndata=60028928_job=21_split=1516.h5
sonyc_ndata=60028928_job=6_split=1910.h5
sonyc_ndata=60028928_job=9_split=774.h5
sonyc_ndata=60028928_job=12_split=925.h5
sonyc_ndata=60028928_job=28_split=1389.h5
sonyc_ndata=60028928_job=17_split=1894.h5
sonyc_ndata=60028928_job=11_split=479.h5
sonyc_ndata=60028928_job=2_split=1364.h5
sonyc_ndata=60028928_job=7_split=597.h5
sonyc_ndata=60028928_job=2_split=684.h5
sonyc_ndata=60028928_job=23_split=1635.h5
sonyc_ndata=60028928_job=2_split=943.h5
sonyc_ndata=60028928_job=7_split=14.h5
sonyc_ndata=60028928_job=15_split=1286.h5
sonyc_ndata=60028928_job=28_split=1648.h5
sonyc_ndata=60028928_job=11_split=6.h5
sonyc_ndata=60028928_job=21_split=803.h5
sonyc_ndata=60028928_job=22_split=1802.h5
sonyc_ndata=60028928_job=29_split=1306.h5
sonyc_ndata=60028928_job=21_split=1384.h5
sonyc_ndata=60028928_job=4_split=690.h5
sonyc_ndata=60028928_job=7_split=19.h5
sonyc_ndata=60028928_job=20_split=1243.h5
sonyc_ndata=60028928_job=9_split=1442.h5
sonyc_ndata=60028

sonyc_ndata=60028928_job=25_split=510.h5
sonyc_ndata=60028928_job=6_split=310.h5
sonyc_ndata=60028928_job=18_split=1297.h5
sonyc_ndata=60028928_job=28_split=12.h5
sonyc_ndata=60028928_job=21_split=1338.h5
sonyc_ndata=60028928_job=27_split=158.h5
sonyc_ndata=60028928_job=1_split=1160.h5
sonyc_ndata=60028928_job=15_split=22.h5
sonyc_ndata=60028928_job=18_split=784.h5
sonyc_ndata=60028928_job=17_split=1533.h5
sonyc_ndata=60028928_job=16_split=1935.h5
sonyc_ndata=60028928_job=30_split=783.h5
sonyc_ndata=60028928_job=30_split=3.h5
sonyc_ndata=60028928_job=16_split=1033.h5
sonyc_ndata=60028928_job=17_split=1876.h5
sonyc_ndata=60028928_job=23_split=1613.h5
sonyc_ndata=60028928_job=29_split=58.h5
sonyc_ndata=60028928_job=14_split=686.h5
sonyc_ndata=60028928_job=21_split=1760.h5
sonyc_ndata=60028928_job=4_split=1377.h5
sonyc_ndata=60028928_job=24_split=791.h5
sonyc_ndata=60028928_job=7_split=810.h5
sonyc_ndata=60028928_job=14_split=1709.h5
sonyc_ndata=60028928_job=13_split=619.h5
sonyc_ndata=60

...

sonyc_ndata=60028928_job=26_split=1592.h5
sonyc_ndata=60028928_job=3_split=1579.h5
sonyc_ndata=60028928_job=11_split=1196.h5
sonyc_ndata=60028928_job=20_split=964.h5
sonyc_ndata=60028928_job=17_split=548.h5
sonyc_ndata=60028928_job=16_split=368.h5
sonyc_ndata=60028928_job=4_split=1204.h5
sonyc_ndata=60028928_job=26_split=11.h5
sonyc_ndata=60028928_job=27_split=1383.h5
sonyc_ndata=60028928_job=16_split=1436.h5
sonyc_ndata=60028928_job=5_split=941.h5
sonyc_ndata=60028928_job=17_split=1634.h5
sonyc_ndata=60028928_job=8_split=53.h5
sonyc_ndata=60028928_job=25_split=1015.h5
sonyc_ndata=60028928_job=22_split=801.h5
sonyc_ndata=60028928_job=17_split=1303.h5
sonyc_ndata=60028928_job=22_split=201.h5
sonyc_ndata=60028928_job=11_split=1010.h5
sonyc_ndata=60028928_job=9_split=1653.h5
sonyc_ndata=60028928_job=30_split=444.h5
sonyc_ndata=60028928_job=20_split=1717.h5
sonyc_ndata=60028928_job=28_split=1741.h5
sonyc_ndata=60028928_job=8_split=1527.h5
sonyc_ndata=60028928_job=1_split=1011.h5
sonyc_ndat

sonyc_ndata=60028928_job=10_split=891.h5
sonyc_ndata=60028928_job=9_split=665.h5
sonyc_ndata=60028928_job=30_split=353.h5
sonyc_ndata=60028928_job=28_split=325.h5
sonyc_ndata=60028928_job=16_split=1398.h5
sonyc_ndata=60028928_job=2_split=1137.h5
sonyc_ndata=60028928_job=14_split=12.h5
sonyc_ndata=60028928_job=20_split=1014.h5
sonyc_ndata=60028928_job=12_split=764.h5
sonyc_ndata=60028928_job=16_split=207.h5
sonyc_ndata=60028928_job=10_split=1111.h5
sonyc_ndata=60028928_job=27_split=1158.h5
sonyc_ndata=60028928_job=10_split=1787.h5
sonyc_ndata=60028928_job=15_split=1179.h5
sonyc_ndata=60028928_job=30_split=1635.h5
sonyc_ndata=60028928_job=10_split=696.h5
sonyc_ndata=60028928_job=10_split=498.h5
sonyc_ndata=60028928_job=21_split=1892.h5
sonyc_ndata=60028928_job=13_split=1380.h5
sonyc_ndata=60028928_job=20_split=977.h5
sonyc_ndata=60028928_job=30_split=854.h5
sonyc_ndata=60028928_job=29_split=1855.h5
sonyc_ndata=60028928_job=12_split=420.h5
sonyc_ndata=60028928_job=2_split=533.h5
sonyc_nda

sonyc_ndata=60028928_job=3_split=1776.h5
sonyc_ndata=60028928_job=27_split=133.h5
sonyc_ndata=60028928_job=16_split=988.h5
sonyc_ndata=60028928_job=24_split=890.h5
sonyc_ndata=60028928_job=17_split=1339.h5
sonyc_ndata=60028928_job=10_split=1107.h5
sonyc_ndata=60028928_job=14_split=1588.h5
sonyc_ndata=60028928_job=1_split=1527.h5
sonyc_ndata=60028928_job=18_split=1546.h5
sonyc_ndata=60028928_job=25_split=578.h5
sonyc_ndata=60028928_job=22_split=520.h5
sonyc_ndata=60028928_job=9_split=146.h5
sonyc_ndata=60028928_job=13_split=1815.h5
sonyc_ndata=60028928_job=7_split=385.h5
sonyc_ndata=60028928_job=9_split=70.h5
sonyc_ndata=60028928_job=13_split=1655.h5
sonyc_ndata=60028928_job=30_split=1436.h5
sonyc_ndata=60028928_job=7_split=1230.h5
sonyc_ndata=60028928_job=13_split=1160.h5
sonyc_ndata=60028928_job=6_split=1697.h5
sonyc_ndata=60028928_job=9_split=315.h5
sonyc_ndata=60028928_job=6_split=311.h5
sonyc_ndata=60028928_job=9_split=515.h5
sonyc_ndata=60028928_job=12_split=754.h5
sonyc_ndata=600

sonyc_ndata=60028928_job=12_split=1492.h5
sonyc_ndata=60028928_job=5_split=193.h5
sonyc_ndata=60028928_job=18_split=431.h5
sonyc_ndata=60028928_job=8_split=1271.h5
sonyc_ndata=60028928_job=5_split=1286.h5
sonyc_ndata=60028928_job=22_split=1745.h5
sonyc_ndata=60028928_job=15_split=1910.h5
sonyc_ndata=60028928_job=14_split=211.h5
sonyc_ndata=60028928_job=23_split=1368.h5
sonyc_ndata=60028928_job=1_split=1677.h5
sonyc_ndata=60028928_job=11_split=112.h5
sonyc_ndata=60028928_job=24_split=745.h5
sonyc_ndata=60028928_job=29_split=1667.h5
sonyc_ndata=60028928_job=30_split=1348.h5
sonyc_ndata=60028928_job=19_split=399.h5
sonyc_ndata=60028928_job=9_split=1178.h5
sonyc_ndata=60028928_job=21_split=1217.h5
sonyc_ndata=60028928_job=15_split=1563.h5
sonyc_ndata=60028928_job=20_split=461.h5
sonyc_ndata=60028928_job=17_split=1380.h5
sonyc_ndata=60028928_job=27_split=954.h5
sonyc_ndata=60028928_job=20_split=1853.h5
sonyc_ndata=60028928_job=18_split=1394.h5
sonyc_ndata=60028928_job=14_split=627.h5
sonyc_

KeyboardInterrupt: 

In [18]:
import h5py
file = '/scratch/mc6591/sonyc_ndata=60028928/sonyc_ndata=60028928_job=11_split=1387.h5'
file = h5py.File(file, 'r')
print(list(file.keys()))

['l3_embedding']


In [19]:
file = '/scratch/cm3580/reduced_embeddings/umap/umap_ndata=2048000_emb=256_nbrs=20_mindist=0.3_mtrc=euclidean/sonyc/sonyc_ndata=60028928_job=11_split=1387.h5'

file = h5py.File(file, 'r')
print(list(file.keys()))

['umap_batch_2048000_len_256_k_20_metric_euclidean_dist|iter_0.3']
